In [2]:
!pip install konlpy
!pip install kiwipiepy
!pip install koeda
!pip install transformers[torch]
!pip install transformers
!pip install datasets
!pip install googletrans==4.0.0-rc1
!pip install pytorch_lightning

  Obtaining dependency information for koeda from https://files.pythonhosted.org/packages/db/4c/cb7daad97e1e2a06b082cea42e93eb106374e439fd2c0e7d817fd0ff5ef3/koeda-0.0.4-py3-none-any.whl.metadata
  Obtaining dependency information for tweepy==3.10.0 from https://files.pythonhosted.org/packages/67/c3/6bed87f3b1e5ed2f34bd58bf7978e308c86e255193916be76e5a5ce5dfca/tweepy-3.10.0-py2.py3-none-any.whl.metadata
  Obtaining dependency information for requests-oauthlib>=0.7.0 from https://files.pythonhosted.org/packages/3b/5d/63d4ae3b9daea098d5d6f5da83984853c1bbacd5dc826764b249fe119d24/requests_oauthlib-2.0.0-py2.py3-none-any.whl.metadata
  Obtaining dependency information for oauthlib>=3.0.0 from https://files.pythonhosted.org/packages/7e/80/cab10959dc1faead58dc8384a781dfbf93cb4d33d50988f7a69f1b7c9bbe/oauthlib-3.2.2-py3-none-any.whl.metadata
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 566.4/566.4 kB 4.0 MB/s eta 0:00:0000:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 151.7/151.7 kB 15.5 MB/

In [5]:
import pandas as pd
import random
from konlpy.tag import Okt
from kiwipiepy import Kiwi
from konlpy.tag import Mecab
import os

### 1. 데이터 읽어오기

In [113]:
# config에 저장된 데이터 경로를 통해 train과 validation data를 불러옵니다.
data_path = '/data/ephemeral/home/data'

# train data의 구조와 내용을 확인합니다.
train_df = pd.read_csv(os.path.join(data_path,'train.csv'))
#train_df.tail()

# validation data의 구조와 내용을 확인합니다.
val_df = pd.read_csv(os.path.join(data_path,'dev.csv'))
#val_df.tail()

In [ ]:
train_df.head(3)
#71386 #Person2# 

In [114]:
ex_data = train_df['dialogue'][8260]
ex_data

'#Person1#: 안녕하세요, 실례지만 무엇을 도와드릴까요?\n#Person2#: 저는 908호의 벨입니다. 방을 바꿔주실 수 있나요? 아내가 밤새 끔찍한 소음 때문에 여러 번 깨어났는데, 그녀가 너무 힘들어하네요.\n#Person1#: 정말 죄송합니다. 908호는 복도 끝에 위치해 있어서 아침 일찍 소음이 들릴 수 있습니다.\n#Person2#: 어쨌든, 방을 바꾸고 싶습니다.\n#Person1#: 문제 없습니다, 저희가 처리하겠습니다.하지만 오늘은 모든 방이 예약되어 있어서, 내일까지 기다려주실 수 있나요?\n#Person2#: 알겠습니다, 내일 저녁에는 조용한 방에서 편안하게 머무르고, 숙면을 취할 수 있기를 바랍니다.\n#Person1#: 네, 그렇게 처리하겠습니다. 더 필요한 것이 있다면 알려주세요.'

In [119]:
import pandas as pd

def augment_dialogue_data(data, repetition=5):
    augmented_data = []
    eda = EasyDataAugmentation(morpheme_analyzer="Okt")

    for dialogue in data:
        dialogue_parts = dialogue.split("#Person")
        augmented_dialogue = ""

        for i, part in enumerate(dialogue_parts):
            if i == 0:
                augmented_dialogue += part
            else:
                person_tag, text = part.split(":", 1)
                if text.strip() == "":  # 빈 문자열 확인
                    print(f"text가 비어있다고 ? {text}")
                    print(f"dialogue {dialogue}")
                    augmented_text = ""
                else:
                    #print(text)
                    augmented_texts = eda(text, p=(0.1, 0.1, 0.1, 0.1), repetition=repetition)
                    if len(augmented_texts) > 0:
                        augmented_text = augmented_texts[0]
                    else:
                        augmented_text = text
                if type(person_tag) == list:
                    person_tag = str(person_tag)
                if type(augmented_text) == list:
                    augmented_text = str(augmented_text)
                augmented_dialogue += "#Person" + person_tag + ": " + augmented_text + " "

        augmented_data.append(augmented_dialogue)

    return augmented_data
augmented_data = augment_dialogue_data([ex_data], repetition=5)
for x in augmented_data:
    print(x)

#Person1#: 안녕하세요, 실례지만 무엇을 도와드릴까요? #Person2#: 저는 908호의 벨입니다. 방을 바꿔주실 수 있나요? 아내가 밤새 끔찍한 때문에 여러 번 깨어났는데, 그녀가 힘들어하네요. #Person1#: 정말 죄송합니다 요행 . 908호는 복도 끝 수익 에 위치해 있어서 아침 일찍 소음이 들릴 수 있습니다. #Person2#: 어쨌든, 방 바꾸고 싶습니다. #Person1#: , 없습니다 저희가 처리하겠습니다.하지만 오늘은 모든 방이 예약되어 있어서, 내일까지 기다려주실문제수 있나요? #Person2#: 알겠습니다, 내일 저녁에는 조용한 방에서 편안하게 머무르고, 숙면을있기를취할 수 바랍니다. #Person1#: 네, 그렇게 처리하겠습니다. 더 필요한 것 있다면 . 


In [120]:
original_data = train_df['dialogue'].tolist()
augmented_data_list = []

for dialogue in original_data:
    augmented_data = augment_dialogue_data([dialogue], repetition=3)
    for aug_dialogue in augmented_data:
        print(f"aug_dialogue : {aug_dialogue}")
        idx = original_data.index(dialogue)
        fname = train_df.loc[idx, 'fname']
        summary = train_df.loc[idx, 'summary']
        topic = train_df.loc[idx, 'topic']
        augmented_data_list.append({'fname' : fname,'dialogue': aug_dialogue, 'summary': summary, 'topic': topic})

# CSV 파일로 저장
df_augmented = pd.DataFrame(augmented_data_list)

df_augmented.to_csv('augmented_data.csv', index=False)

aug_dialogue : #Person1#: 안녕하세요, 닥터 스미스씨. 저는 호킨스 의사입니다. 오늘 왜 오셨나요? #Person2#: 건강검진을 받는 것좋을 이 것 같아서요. #Person1#: 그렇군요, 당신은 5년 동안건강검진 을 받지 않았습니다. 매년 받아야 합니다. #Person2#: 의원 알고 있습니다. 하지만 아무 문제가 없다면 왜 의사를 만나러 가야 하나요? #Person1#: 심각한 질병을 피하는 피해 가장 좋은 방법은 이를 조기에 발견하는 것입니다. 그러니 당신의 건강을 백금 위해 최소한 체 매년 한 번은 오세요. #Person2#: .알겠습니다 #Person1#: 여기 보세요. 당신의 눈과 귀는 괜찮아 보입니다.스미스깊게 숨을?들이쉬세요. 씨, 담배 피우시나요 #Person2#: 네. #Person1#: 당신도 알다시피, 담배는 폐암과 심장병 교과 의 주요 원인입니다. 정말로 끊으셔야 합니다. #Person2#: 수백 번 시도했지만, 습관을 버리는 것이 어렵습니다. #Person1#: 우리는 도움이 될 수 있는 수업 약물들 제공하고 있습니다. 나가기 전에 더 많은 정보를 드리겠습니다. #Person2#: 알겠습니다, 감사합니다 군의관 , 의사선생님. 
aug_dialogue : #Person1#: 안녕하세요, 파커 와이프, 어떻게 지내셨나요? #Person2#: 안녕하세요, 피터스 박사님백신 잘 지냈습니다, 감사합니다. 리키와 함께 . 접종을 위해 왔습니다. #Person1#: 좋습니다. 백신 기록을 보니, 리키는 이미 소아마비, 디프테리아, 형 간염 백신을 맞았군요. 그 14개월이므로, 이제 A형 간염, 수두, 홍역 백신 맞아야 합니다. #Person2#: 티끌과 볼거리는 어떻게 되나요? #Person1#: 지금은 이 백신들만 접종 수 있고, 몇 주 후에 나머지를 접종할할수 있습니다. #Person2#: 좋습니다. 박사님, 극 저도 디프테리아 예방접종이 필요할 것 같아요. 마지막 인간 으로 맞은 게 아마도 15년 전이었던 것 같아요! 

In [69]:
from koeda import AEasierDataAugmentation
#https://catsirup.github.io/ai/2020/04/21/nlp_data_argumentation.html
def augment_text_data_with_AEDA(text, repetition):
    """입력된 문장에 대해서 AEDA를 통해 데이터 증강"""
    aeda = AEasierDataAugmentation(
        morpheme_analyzer="Okt", punctuations=[".", ",", "!", "?", ";", ":"]
    )

    result = aeda(text, p=0.3, repetition=repetition)

    # 증강 결과 출력
    print("원문: " , text)
    print("--"*100)
    for i in range(repetition):
        print(f"증강문{i+1}: ", result[i])
    # return result

In [ ]:
import pandas as pd
from koeda import AEasierDataAugmentation

def augment_dialogue_data(data, repetition=5):
    augmented_data = []
    aeda = AEasierDataAugmentation(morpheme_analyzer="Okt", punctuations=[".", ",", "!", "?", ";", ":"])

    for dialogue in data:
        dialogue_parts = dialogue.split("#Person")
        augmented_dialogue = ""

        for i, part in enumerate(dialogue_parts):
            if i == 0:
                augmented_dialogue += part
            else:
                person_tag, text = part.split(":", 1)
                augmented_texts = aeda(text, p=0.3, repetition=repetition)
                if len(augmented_texts) > 0:
                    augmented_text = augmented_texts[0]
                else:
                    augmented_text = text
                augmented_dialogue += "#Person" + person_tag + ": " + augmented_text
        augmented_data.append(augmented_dialogue)
    return augmented_data

augmented_data = augment_dialogue_data([ex_data], repetition=3)

print("원본 데이터:")
print(ex_data)
print("\n증강된 데이터:")
for data in augmented_data:
    print(data)

In [ ]:
from googletrans import Translator

def augment_text_data_with_BT(text,repetition):
    """입력된 문장에 대해서 BT를 통해 데이터 증강"""
    # Translator 객체 생성
    translator = Translator()
    result = []

    # 번역 실행 (한국어 > 영어 > 한국어)
    for i in range(repetition):
        translated = translator.translate(text, src='ko', dest='en')
        re_translated = translator.translate(translated.text, src='en', dest='ko')
        result.append(re_translated.text)

    # 번역 결과 출력
    print("원문: " , text)
    print("--"*100)
    for i in range(repetition):
        print(f"증강문{i+1}: ", result[i])
    # return result

In [ ]:
import pandas as pd
from googletrans import Translator

def augment_dialogue_data_with_BT(data, repetition=5):
    augmented_data = []
    translator = Translator()

    for dialogue in data:
        dialogue_parts = dialogue.split("#Person")
        augmented_dialogue = ""

        for i, part in enumerate(dialogue_parts):
            if i == 0:
                augmented_dialogue += part
            else:
                person_tag, text = part.split(":", 1)
                augmented_texts = []

                # 번역 실행 (한국어 > 영어 > 한국어)
                for _ in range(repetition):
                    translated = translator.translate(text, src='ko', dest='en')
                    re_translated = translator.translate(translated.text, src='en', dest='ko')
                    augmented_texts.append(re_translated.text)

                if len(augmented_texts) > 0:
                    augmented_text = augmented_texts[0]
                else:
                    augmented_text = text

                augmented_dialogue += "#Person" + person_tag + ": " + augmented_text

        augmented_data.append(augmented_dialogue)

    return augmented_data

# 예시 데이터
train_df = pd.DataFrame({"dialogue": ["#Person1#: 실례합니다, 열쇠 한 묶음 보셨나요? #Person2#: 어떤 종류의 열쇠인가요? #Person1#: 5개의 열쇠와 작은 발 장식이 있어요. #Person2#: 안타깝네요! 저는 보지 못했습니다. #Person1#: 그럼, 찾는 데 도와주실 수 있나요? 제가 여기는 처음이라서요. #Person2#: 물론입니다. 기꺼이 도와드리겠습니다. 사라진 열쇠를 찾는 데 도와드리겠습니다. #Person1#: 정말 친절하시네요."]})

ex_data = train_df['dialogue'][0]
augmented_data = augment_dialogue_data_with_BT([ex_data], repetition=3)

print("원본 데이터:")
print(ex_data)
print("\n증강된 데이터:")
for data in augmented_data:
    print(data)

In [ ]:
import pandas as pd
from googletrans import Translator

def augment_dialogue_data_with_BT(data, repetition=5):
    augmented_data = []
    translator = Translator()

    for dialogue in data:
        dialogue_parts = dialogue.split("#Person")
        augmented_dialogue = ""

        for i, part in enumerate(dialogue_parts):
            if i == 0:
                augmented_dialogue += part
            else:
                person_tag, text = part.split(":", 1)
                augmented_texts = []

                # 번역 실행 (한국어 > 영어 > 한국어)
                for _ in range(repetition):
                    translated = translator.translate(text, src='ko', dest='en')
                    re_translated = translator.translate(translated.text, src='en', dest='ko')
                    augmented_texts.append(re_translated.text)

                if len(augmented_texts) > 0:
                    augmented_text = augmented_texts[0]
                else:
                    augmented_text = text

                augmented_dialogue += "#Person" + person_tag + ": " + augmented_text

        augmented_data.append(augmented_dialogue)

    return augmented_data

augmented_data = augment_dialogue_data_with_BT([ex_data], repetition=3)

print("원본 데이터:")
print(ex_data)
print("\n증강된 데이터:")
for data in augmented_data:
    print(data)